<a href="https://colab.research.google.com/github/midokorg/VAE-Diffusion-TDI/blob/main/VAE_Diffusion_IEEE.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [6]:
# --- imports (les tiens) ---
import os
import random
import joblib
import numpy as np
import pandas as pd
from PIL import Image
from tqdm.auto import tqdm

import torch
from torch import nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader, Subset

from torchvision import transforms as T, models
from diffusers import UNet2DConditionModel, DDPMScheduler, DPMSolverMultistepScheduler
from pytorch_msssim import MS_SSIM
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.model_selection import StratifiedKFold

# --- paramètres globaux (les tiens) ---
seed    = 42
random.seed(seed); np.random.seed(seed); torch.manual_seed(seed)
DEVICE  = torch.device("cuda" if torch.cuda.is_available() else "cpu")
USE_AMP = True
early_stop_patience = 40

# Drive mount etc. (tes chemins)
from google.colab import drive
drive.mount('/content/drive', force_remount=True)

BASE_DIR       = '/content/drive/MyDrive/colab'
DATA_IMG_DIR   = os.path.join(BASE_DIR, 'DATATDI')
CLINICAL_CSV   = os.path.join(BASE_DIR, 'BC_cardiotox_clinical.csv')
MODEL_SAVE_DIR = os.path.join(BASE_DIR, 'vae_analysis')
os.makedirs(MODEL_SAVE_DIR, exist_ok=True)

# hyperparams
IMAGE_SIZE       = (160, 384)
BATCH_SIZE       = 64
LR               = 5e-5
EPOCHS           = 200
TIMESTEPS_COARSE = 100
TIMESTEPS_FINE   = 1000
THRESH_EPOCH     = int(EPOCHS * 0.8)
GUIDANCE_SCALE   = 4.0
NUM_WORKERS      = 0

LAMBDA_PERC_DIFF = 0.1
LAMBDA_SSIM_DIFF = 1.0

# transforms (les tiens)
augment_tf = T.Compose([
    T.ColorJitter(0.2,0.2,0.2,0.1),
    T.RandomHorizontalFlip(),
    T.RandomRotation(10),
    T.Resize(IMAGE_SIZE),
])
base_tf = T.Compose([
    T.Grayscale(num_output_channels=1),
    T.ToTensor(),
    T.Normalize([0.5], [0.5]),
])

# --- ConvVAE (inchangé) ---
class ConvVAE(nn.Module):
    def __init__(self, latent_dim, img_size):
        super().__init__()
        self.act, self.out_act = nn.ReLU(), nn.Tanh()
        self.enc1 = nn.Conv2d(1,32,4,2,1)
        self.enc2 = nn.Conv2d(32,64,4,2,1)
        self.enc3 = nn.Conv2d(64,128,4,2,1)
        self.enc4 = nn.Conv2d(128,256,4,2,1)
        with torch.no_grad():
            dummy = torch.zeros(1,1,*img_size)
            h     = self._encode_layers(dummy)
            self.conv_shape = h.shape[1:]
            flat_dim       = int(np.prod(self.conv_shape))
        self.fc_mu     = nn.Linear(flat_dim, latent_dim)   # latent_dim used here
        self.fc_logvar = nn.Linear(flat_dim, latent_dim)
        self.fc_dec    = nn.Linear(latent_dim, flat_dim)
        self.dec4 = nn.ConvTranspose2d(256,128,4,2,1)
        self.dec3 = nn.ConvTranspose2d(128,64,4,2,1)
        self.dec2 = nn.ConvTranspose2d(64,32,4,2,1)
        self.dec1 = nn.ConvTranspose2d(32,1,4,2,1)

    def _encode_layers(self, x):
        e1 = self.act(self.enc1(x))
        e2 = self.act(self.enc2(e1))
        e3 = self.act(self.enc3(e2))
        e4 = self.act(self.enc4(e3))
        return e4

    def forward(self, x):
        e4   = self._encode_layers(x)
        flat = e4.flatten(1)
        mu, logvar = self.fc_mu(flat), self.fc_logvar(flat)
        return mu, logvar, e4

    def decode(self, h):
        d1 = self.act(self.dec4(h.view(-1, *self.conv_shape)))
        d2 = self.act(self.dec3(d1))
        d3 = self.act(self.dec2(d2))
        return self.out_act(self.dec1(d3))

# charger vae pretrained
vae = ConvVAE(latent_dim=256, img_size=IMAGE_SIZE).to(DEVICE)
vae.load_state_dict(torch.load(os.path.join(BASE_DIR,'vae_analysis','vae_tdi_perc.pt'),
                              map_location=DEVICE))
vae.eval()

# --- LatentDataset (robuste aux images manquantes) ---
class LatentDataset(Dataset):
    def __init__(self, df, data_dir, device, scaler=None, encoders=None, augment=False):
        """
        df: pandas DataFrame déjà filtré (subset train/val)
        scaler: StandardScaler fit sur le train (None -> fit on df)  # in your code you pass scaler_train
        encoders: dict of LabelEncoders (fit globally once)
        augment: whether to apply augmentation (train)
        """
        self.df = df.copy().reset_index(drop=True)
        self.data_dir = data_dir
        self.device = device
        self.augment = augment

        # numeric & categorical columns (same as before)
        self.num_cols = ['age','weight','height','time','LVEF','heart_rate','PWT','LAd','LVDd','LVSd']
        self.cat_cols = ['heart_rhythm','AC','antiHER2','ACprev','antiHER2prev','HTA','DL',
                         'DM','smoker','exsmoker','RTprev','CIprev','ICMprev','ARRprev',
                         'VALVprev','cxvalv']

        # Ensure numeric conversion in the DataFrame (but we will transform per-row using scaler)
        self.df[self.num_cols] = self.df[self.num_cols].replace(',', '.', regex=True).astype(float)

        # scaler must be provided (you fit it on train before creating the dataset)
        if scaler is None:
            # fallback: fit on available rows in df (not ideal for k-fold where you should pass scaler)
            self.scaler = StandardScaler().fit(self.df[self.num_cols].values)
        else:
            self.scaler = scaler

        # encoders: if None, fit on this df (but in your pipeline you pass GLOBAL_ENCODERS)
        if encoders is None:
            self.encoders = {}
            for c in self.cat_cols:
                le = LabelEncoder().fit(self.df[c].fillna('0').astype(str).values)
                self.encoders[c] = le
        else:
            self.encoders = encoders

        # Now iterate rows, encode clinical per-row using provided scaler/encoders,
        # and encode image to latent using pretrained VAE.
        latents = []
        clinical_rows = []
        labels = []
        skipped = 0

        for i, row in self.df.iterrows():
            pid = str(row['patient_id'])
            lbl = int(row['CTRCD'])
            sub = 'CTRCD' if lbl == 1 else 'NO_CTRCD'
            path = os.path.join(self.data_dir, sub, f"image ({pid}).png")

            # check existence & readability
            if not os.path.exists(path):
                skipped += 1
                # optional: print(f"Warning: image not found for patient {pid} -> skipping")
                continue

            try:
                img = Image.open(path).convert('RGB')
            except Exception as e:
                skipped += 1
                # optional: print(f"Warning: cannot open image for patient {pid} ({e}) -> skipping")
                continue

            # image transforms
            if self.augment:
                img_t = augment_tf(img)
            else:
                img_t = T.Resize(IMAGE_SIZE)(img)
            x = base_tf(img_t).unsqueeze(0).to(self.device)

            # encode with vae (we only need the latent feature map e4)
            with torch.no_grad():
                _, _, h = vae(x)
            latents.append(h.squeeze(0).cpu())

            # build clinical vector: scale numeric, encode categoricals
            num_vals = row[self.num_cols].values.reshape(1, -1)
            num_scaled = self.scaler.transform(num_vals)[0]

            cat_vals = []
            for c in self.cat_cols:
                raw = str(row[c]) if pd.notna(row[c]) else '0'
                # ensure encoder can handle unseen by mapping unknowns to '0' label if necessary
                try:
                    enc_v = self.encoders[c].transform([raw])[0]
                except Exception:
                    # fallback: try fitting/using label '0' mapping if present
                    try:
                        enc_v = self.encoders[c].transform([ '0' ])[0]
                    except Exception:
                        # if encoder totally incompatible, set 0
                        enc_v = 0
                cat_vals.append(enc_v)

            clinical_vec = np.concatenate([num_scaled, np.array(cat_vals, dtype=float)], axis=0)
            clinical_rows.append(clinical_vec)
            labels.append(lbl)

        if len(latents) == 0:
            raise RuntimeError("No valid images found for this dataset (all missing or unreadable).")

        self.lats = torch.stack(latents)                    # [N, C, H, W]
        self.clinical = torch.tensor(np.stack(clinical_rows), dtype=torch.float32)
        self.labels = torch.tensor(labels, dtype=torch.long)

        if skipped > 0:
            print(f"LatentDataset: {skipped} row(s) skipped because image missing/corrupt. {len(self.lats)} samples loaded.")

    def __len__(self): return len(self.lats)
    def __getitem__(self, idx): return self.lats[idx], self.clinical[idx], self.labels[idx]


# --- Préparer le DataFrame global et les encoders globaux ---
df_all = pd.read_csv(CLINICAL_CSV, on_bad_lines='skip', sep=';')
df_all['patient_id'] = df_all['patient_id'].astype(str)

# Fit global label encoders once (pour stabilité)
cat_cols = ['heart_rhythm','AC','antiHER2','ACprev','antiHER2prev','HTA','DL',
            'DM','smoker','exsmoker','RTprev','CIprev','ICMprev','ARRprev',
            'VALVprev','cxvalv']
GLOBAL_ENCODERS = {}
for c in cat_cols:
    le = LabelEncoder().fit(df_all[c].fillna('0').astype(str).values)
    GLOBAL_ENCODERS[c] = le

# --- K-fold setup ---
K = 5
skf = StratifiedKFold(n_splits=K, shuffle=True, random_state=seed)
X_idx = np.arange(len(df_all))
y_all = df_all['CTRCD'].astype(int).values

fold_results = []

for fold, (train_idx, val_idx) in enumerate(skf.split(X_idx, y_all), start=1):
    print(f"\n=== Fold {fold}/{K} ===")
    df_train = df_all.iloc[train_idx].reset_index(drop=True)
    df_val   = df_all.iloc[val_idx].reset_index(drop=True)

    # Fit scaler only on train numeric cols
    num_cols = ['age','weight','height','time','LVEF','heart_rate','PWT','LAd','LVDd','LVSd']
    scaler_train = StandardScaler().fit(df_train[num_cols].replace(',', '.', regex=True).astype(float).values)

    # Datasets
    print("Image data directory:", DATA_IMG_DIR) # Print image directory
    train_ds = LatentDataset(df_train, DATA_IMG_DIR, DEVICE, scaler=scaler_train, encoders=GLOBAL_ENCODERS, augment=True)
    val_ds   = LatentDataset(df_val,   DATA_IMG_DIR, DEVICE, scaler=scaler_train, encoders=GLOBAL_ENCODERS, augment=False)

    train_loader = DataLoader(train_ds, batch_size=BATCH_SIZE, shuffle=True, num_workers=NUM_WORKERS)
    val_loader   = DataLoader(val_ds,   batch_size=BATCH_SIZE, shuffle=False, num_workers=NUM_WORKERS)

    # Build UNet model fresh per fold (réinitialise les poids)
    C, Hf, Wf = train_ds.lats.shape[1:]  # [N,C,H,W] -> shape
    model = UNet2DConditionModel(
        sample_size         = (Hf, Wf),
        in_channels         = C,
        out_channels        = C,
        down_block_types    = ("DownBlock2D",)*4,
        up_block_types      = ("UpBlock2D",)*4,
        block_out_channels  = (128,256,512,1024),
        cross_attention_dim = train_ds.clinical.shape[1],
    ).to(DEVICE)

    noise_scheduler = DDPMScheduler(num_train_timesteps=TIMESTEPS_COARSE)
    sampling_scheduler = DPMSolverMultistepScheduler.from_config(noise_scheduler.config)
    sampling_scheduler.set_timesteps(TIMESTEPS_COARSE)

    optimizer = torch.optim.AdamW(model.parameters(), lr=LR)
    lr_scheduler= torch.optim.lr_scheduler.ReduceLROnPlateau(
        optimizer, mode='min', factor=0.5, patience=10, min_lr=1e-7
    )

    mse_fn = nn.MSELoss()
    ssim_fn = MS_SSIM(data_range=2.0, channel=1, size_average=True, win_size=7)
    scaler_amp = torch.amp.GradScaler(enabled=USE_AMP)

    # Perceptual VGG (comme toi)
    vgg = models.vgg16(weights=models.VGG16_Weights.IMAGENET1K_V1).features[:16].to(DEVICE).eval()
    for p in vgg.parameters(): p.requires_grad = False
    def perceptual_loss(img_pred, img_gt):
        fp = vgg(img_pred.repeat(1,3,1,1))
        fg = vgg(img_gt.repeat(1,3,1,1))
        return F.mse_loss(fp, fg)

    # training loop (identique à ton original mais scope local)
    best_val = float('inf'); no_improve = 0
    for epoch in range(1, EPOCHS+1):
        if epoch == THRESH_EPOCH:
            noise_scheduler    = DDPMScheduler(num_train_timesteps=TIMESTEPS_FINE)
            sampling_scheduler = DPMSolverMultistepScheduler.from_config(noise_scheduler.config)
            sampling_scheduler.set_timesteps(TIMESTEPS_FINE)

        model.train()
        for lat, conds, _ in tqdm(train_loader, desc=f"[Fold {fold}] Train {epoch}/{EPOCHS}"):
            lat = lat.to(DEVICE)
            conds = conds.unsqueeze(1).to(DEVICE)

            noise = torch.randn_like(lat)
            ts    = torch.randint(0, noise_scheduler.config.num_train_timesteps,
                                  (lat.size(0),), device=DEVICE)
            noisy = noise_scheduler.add_noise(lat, noise, ts)

            with torch.amp.autocast(device_type="cuda", enabled=USE_AMP):
                uncond   = model(noisy, ts, encoder_hidden_states=torch.zeros_like(conds)).sample
                cond     = model(noisy, ts, encoder_hidden_states=conds).sample
                eps      = uncond + GUIDANCE_SCALE * (cond - uncond)
                loss_mse = mse_fn(eps, noise)

                alphas = torch.tensor(noise_scheduler.alphas_cumprod, device=DEVICE)
                a_t    = alphas[ts].view(-1,1,1,1)
                x0_pred = (noisy - torch.sqrt(1 - a_t)*eps) / torch.sqrt(a_t)

                recon_pred = vae.decode(x0_pred)
                recon_gt   = vae.decode(lat)

                loss_perc = perceptual_loss(recon_pred, recon_gt)
                rp, rg    = recon_pred + 1.0, recon_gt + 1.0
                loss_ssim = 1 - ssim_fn(rp, rg)

                loss = loss_mse + LAMBDA_PERC_DIFF * loss_perc + LAMBDA_SSIM_DIFF * loss_ssim

            scaler_amp.scale(loss).backward()
            nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
            scaler_amp.step(optimizer); scaler_amp.update(); optimizer.zero_grad()

        # validation per epoch
        model.eval()
        sum_mse, sum_ssim, sum_psnr, n = 0,0,0,0
        with torch.no_grad():
            for lat, conds, _ in val_loader:
                lat   = lat.to(DEVICE)
                conds = conds.unsqueeze(1).to(DEVICE)

                noise = torch.randn_like(lat)
                ts    = torch.randint(0, noise_scheduler.config.num_train_timesteps,
                                      (lat.size(0),), device=DEVICE)
                noisy = noise_scheduler.add_noise(lat, noise, ts)

                uncond = model(noisy, ts, encoder_hidden_states=torch.zeros_like(conds)).sample
                cond   = model(noisy, ts, encoder_hidden_states=conds).sample
                eps    = uncond + GUIDANCE_SCALE * (cond - uncond)

                prevs = [
                    noise_scheduler.step(eps[i:i+1], int(ts[i]), noisy[i:i+1]).prev_sample
                    for i in range(lat.size(0))
                ]
                recon_lat = torch.cat(prevs, 0)

                mse_v  = mse_fn(recon_lat, lat).item()
                recon_img = vae.decode(recon_lat)
                gt_img    = vae.decode(lat)
                rp, rg    = recon_img + 1.0, gt_img + 1.0

                ssim_v    = ssim_fn(rp, rg).item()
                psnr_v    = 10 * torch.log10(torch.tensor(1.0 / (mse_v + 1e-12))).item()

                sum_mse  += mse_v * lat.size(0)
                sum_ssim += ssim_v * lat.size(0)
                sum_psnr += psnr_v * lat.size(0)
                n        += lat.size(0)

        avg_mse  = sum_mse / n
        avg_ssim = sum_ssim / n
        avg_psnr = sum_psnr / n
        print(f"[Fold {fold}] Val {epoch:03d}: MSE={avg_mse:.4f}, SSIM={avg_ssim:.4f}, PSNR={avg_psnr:.2f}dB")

        lr_scheduler.step(avg_mse)
        if avg_mse < best_val:
            best_val, no_improve = avg_mse, 0
            torch.save(model.state_dict(), os.path.join(MODEL_SAVE_DIR,f'best_model_fold{fold}.pt'))
            joblib.dump(train_ds.scaler,        os.path.join(MODEL_SAVE_DIR,f'scaler_fold{fold}.joblib'))
            joblib.dump(train_ds.encoders,os.path.join(MODEL_SAVE_DIR,f'encoders_fold{fold}.joblib'))
            print("→ Nouveau best enregistré (fold {})".format(fold))
        else:
            no_improve += 1
            if no_improve >= early_stop_patience:
                print("→ Early stopping fold", fold)
                break

    # save metrics summary for fold
    fold_results.append({'fold':fold, 'val_mse':best_val, 'final_ssim':avg_ssim, 'final_psnr':avg_psnr})

print("\n=== K-Fold Summary ===")
for r in fold_results:
    print(r)
print("🏁 Tous les folds terminés. Modèles sauvegardés dans", MODEL_SAVE_DIR)

Mounted at /content/drive

=== Fold 1/5 ===
Image data directory: /content/drive/MyDrive/colab/DATATDI
LatentDataset: 21 row(s) skipped because image missing/corrupt. 115 samples loaded.
LatentDataset: 4 row(s) skipped because image missing/corrupt. 30 samples loaded.


[Fold 1] Train 1/200:   0%|          | 0/2 [00:00<?, ?it/s]

/tmp/ipython-input-1558420429.py:321: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.detach().clone() or sourceTensor.detach().clone().requires_grad_(True), rather than torch.tensor(sourceTensor).
  alphas = torch.tensor(noise_scheduler.alphas_cumprod, device=DEVICE)


[Fold 1] Val 001: MSE=0.2275, SSIM=0.8150, PSNR=6.43dB
→ Nouveau best enregistré (fold 1)


[Fold 1] Train 2/200:   0%|          | 0/2 [00:00<?, ?it/s]

...

[Fold 5] Val 064: MSE=0.2344, SSIM=0.8061, PSNR=6.30dB


[Fold 5] Train 65/200:   0%|          | 0/2 [00:00<?, ?it/s]

[Fold 5] Val 065: MSE=0.2241, SSIM=0.8193, PSNR=6.50dB


[Fold 5] Train 66/200:   0%|          | 0/2 [00:00<?, ?it/s]

[Fold 5] Val 066: MSE=0.2619, SSIM=0.7890, PSNR=5.82dB
→ Early stopping fold 5

=== K-Fold Summary ===
{'fold': 1, 'val_mse': 0.1726139336824417, 'final_ssim': 0.8066995143890381, 'final_psnr': 6.598232388496399}
{'fold': 2, 'val_mse': 0.1733406037092209, 'final_ssim': 0.7873947620391846, 'final_psnr': 5.589050054550171}
{'fold': 3, 'val_mse': 0.1952514946460724, 'final_ssim': 0.7738779783248901, 'final_psnr': 5.281318426132202}
{'fold': 4, 'val_mse': 0.1949743926525116, 'final_ssim': 0.7709294557571411, 'final_psnr': 5.273698568344116}
{'fold': 5, 'val_mse': 0.19252373278141022, 'final_ssim': 0.7890085577964783, 'final_psnr': 5.819449424743652}
🏁 Tous les folds terminés. Modèles sauvegardés dans /content/drive/MyDrive/colab/vae_analysis


In [2]:
!pip install diffusers
!pip install pytorch-msssim # Install the missing 'pytorch-msssim' package.

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.1/4.1 MB 47.8 MB/s eta 0:00:00
